In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [2]:
import warnings
warnings.filterwarnings("ignore")

import argparse 
import torch

from datasets import load_dataset
from transformers import AutoImageProcessor
from lens import HookedVisionTransformer

VisionTransformer

In [3]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# load a model (e.g. ViT Base)
model_name_or_path = "google/vit-base-patch16-224"
model = HookedVisionTransformer.from_pretrained(model_name_or_path, device)
image_processor = AutoImageProcessor.from_pretrained(model_name_or_path)
dataset = load_dataset(
    "cifar10",
    cache_dir="./../cache",
    task="image-classification"
)

# create random boolean mask of shape (batch_size, n_patches)
n_patches = (model.config.image_size // model.config.patch_size) ** 2
bool_masked_pos = torch.randint(low=0, high=2, size=(1, n_patches)).bool().to(device)

# extract image features
features = image_processor(images=dataset['test']['image'][0], return_tensors="pt")
features.to(device)

# run the model and get outputs and activations
outputs, activations = model.run_with_cache(**features, bool_masked_pos=bool_masked_pos)

Some weights of ViTForMaskedImageModeling were not initialized from the model checkpoint at google/vit-base-patch16-224 and are newly initialized: ['decoder.0.weight', 'decoder.0.bias', 'vit.embeddings.mask_token']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [4]:
activations.keys()

dict_keys(['embeddings', 'encoder.0.ln1', 'encoder.0.attn.q', 'encoder.0.attn.k', 'encoder.0.attn.v', 'encoder.0.ln2', 'encoder.0.intermediate', 'encoder.1.ln1', 'encoder.1.attn.q', 'encoder.1.attn.k', 'encoder.1.attn.v', 'encoder.1.ln2', 'encoder.1.intermediate', 'encoder.2.ln1', 'encoder.2.attn.q', 'encoder.2.attn.k', 'encoder.2.attn.v', 'encoder.2.ln2', 'encoder.2.intermediate', 'encoder.3.ln1', 'encoder.3.attn.q', 'encoder.3.attn.k', 'encoder.3.attn.v', 'encoder.3.ln2', 'encoder.3.intermediate', 'encoder.4.ln1', 'encoder.4.attn.q', 'encoder.4.attn.k', 'encoder.4.attn.v', 'encoder.4.ln2', 'encoder.4.intermediate', 'encoder.5.ln1', 'encoder.5.attn.q', 'encoder.5.attn.k', 'encoder.5.attn.v', 'encoder.5.ln2', 'encoder.5.intermediate', 'encoder.6.ln1', 'encoder.6.attn.q', 'encoder.6.attn.k', 'encoder.6.attn.v', 'encoder.6.ln2', 'encoder.6.intermediate', 'encoder.7.ln1', 'encoder.7.attn.q', 'encoder.7.attn.k', 'encoder.7.attn.v', 'encoder.7.ln2', 'encoder.7.intermediate', 'encoder.8.ln1'

In [5]:
import math
import plotly.express as px
import torch.nn as nn

def transpose_for_scores(x: torch.Tensor) -> torch.Tensor:
    attention_head_size = int(model.config.hidden_size / model.config.num_attention_heads)
    new_x_shape = x.size()[:-1] + (model.config.num_attention_heads, attention_head_size)
    x = x.view(new_x_shape)
    return x.permute(0, 2, 1, 3)

def compute_attention_patterns(activations: dict, layer: int):

    key_layer = transpose_for_scores(activations[f"encoder.{layer}.attn.k"])
    query_layer = transpose_for_scores(activations[f"encoder.{layer}.attn.q"])

    # take the dot product between "query" and "key" to get the raw attention scores
    attention_scores = torch.matmul(query_layer, key_layer.transpose(-1, -2))
    attention_scores = attention_scores / math.sqrt(int(model.config.hidden_size / model.config.num_attention_heads))

    # normalize the attention scores to probabilities
    attention_probs = nn.functional.softmax(attention_scores, dim=-1)
    return attention_probs.cpu()


def display_attention_head(layer:int, head: int):

    attention_patterns = compute_attention_patterns(activations, layer)  # shape: (batch_size, n_heads, seq_len, seq_len)

    attention_pattern = attention_patterns[0, head, :, :]
    fig = px.imshow(
        attention_pattern,
        title=f"Attention Pattern of Head {head}",
        color_continuous_scale='RdBu_r',
        zmin=-1, zmax=1,
        height=600, width=600
    )
    fig.show()


display_attention_head(0, 0)

In [6]:
layer_to_ablate = 0
head_index_to_ablate = 0
def head_ablation_hook(value, hook):
    
    # convert (batch_size, seq_len, d_model) to (batch_size, n_heads, seq_len, d_head)
    value = transpose_for_scores(value)

    # zero-ablate an attention head
    value[:, head_index_to_ablate, :, :] = 0.

    # convert (batch_size, n_heads, sew_len, d_head) to (batch_size, seq_len, d_model)
    value = value.permute(0, 2, 1, 3).flatten(2, 3)
    return value


original_loss = model(**features, bool_masked_pos=bool_masked_pos, return_dict=True)["loss"]
ablated_loss = model.run_with_hooks(
    **features,
    bool_masked_pos=bool_masked_pos,
    fwd_hooks=[(
        "encoder.0.attn.v",
        head_ablation_hook
        )]
    )["loss"]
print(f"Original Loss: {original_loss.item():.3f}")
print(f"Ablated Loss: {ablated_loss.item():.3f}")

Original Loss: 0.476
Ablated Loss: 0.496


CLIP

In [3]:
from PIL import Image
import requests

from transformers import CLIPProcessor


device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# load a model (e.g. ViT Base)
model_name_or_path = "openai/clip-vit-base-patch32"
model = HookedVisionTransformer.from_pretrained(model_name_or_path, device)
processor = CLIPProcessor.from_pretrained(model_name_or_path)

url = "http://images.cocodataset.org/val2017/000000039769.jpg"
image = Image.open(requests.get(url, stream=True).raw)

# extract image features
inputs = processor(text=["a photo of a cat", "a photo of a dog"], images=image, return_tensors="pt", padding=True)
inputs.to(device)

# run the model and get outputs and activations
outputs, activations = model.run_with_cache(**inputs)

In [5]:
activations.keys()

dict_keys(['vision_embeddings', 'vision_model.ln1', 'vision_model.0.ln1', 'vision_model.0.attn_q', 'vision_model.0.attn_k', 'vision_model.0.attn_v', 'vision_model.0.attn_z', 'vision_model.0.ln2', 'vision_model.0.mlp.fc1', 'vision_model.0.mlp.act_fn', 'vision_model.0.mlp.fc2', 'vision_model.1.ln1', 'vision_model.1.attn_q', 'vision_model.1.attn_k', 'vision_model.1.attn_v', 'vision_model.1.attn_z', 'vision_model.1.ln2', 'vision_model.1.mlp.fc1', 'vision_model.1.mlp.act_fn', 'vision_model.1.mlp.fc2', 'vision_model.2.ln1', 'vision_model.2.attn_q', 'vision_model.2.attn_k', 'vision_model.2.attn_v', 'vision_model.2.attn_z', 'vision_model.2.ln2', 'vision_model.2.mlp.fc1', 'vision_model.2.mlp.act_fn', 'vision_model.2.mlp.fc2', 'vision_model.3.ln1', 'vision_model.3.attn_q', 'vision_model.3.attn_k', 'vision_model.3.attn_v', 'vision_model.3.attn_z', 'vision_model.3.ln2', 'vision_model.3.mlp.fc1', 'vision_model.3.mlp.act_fn', 'vision_model.3.mlp.fc2', 'vision_model.4.ln1', 'vision_model.4.attn_q', '